In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import sklearn.datasets
import matplotlib.cm
from scipy.cluster.hierarchy import dendrogram

import sklearn.cluster

# Clustering hierarchique

Dans ce TP, nous allons explorer les méthodes de clustering hierarchique.
Nous n'allons pas ré-implémenter nous même ces algorithmes, nous allons à la place utiliser la librairie scikit-learn : https://scikit-learn.org/stable/
Celle-ci est déjà installée sur les machines de l'université.
Si vous utilisez votre machine personnelle, il faudra d'abord vérifier que la librairie est correctement installée.


## 1. Quelques rappels de Python

Les données que nous manipulerons dans ce TP seront représentées sous la forme d'un array numpy (une matrice).
Ces matrices seront des matrices où :

- chaque ligne correspond à un point des données
- chaque colonne correspond à une dimension des données.

Par exemples, pour un jeu de données contenant 3 points en 2 dimensions, nous aurons une matrice de 3 lignes et 2 colonnes.
Un exemple est donné ci-dessous.

In [ ]:
# création d'un jeu de données avec 3 points en 2 dimensions
X_example = np.array([
    [1., 1.],  # premier point des données
    [2., 1.],  # deuxième point des données
    [2., 1.2]  # troisième point des données
])

# Affiche les dimensions de la matrice
print(X_example.shape)

In [ ]:
# Pour récupérer un point en particulier,

X_example[1]

In [ ]:
# Vous pouvez également récupérer tout une colonne d'un coup,
# cela sera utile pour afficher les résultats dans des graphes

print("Première colonne :", X_example[:, 0])
print("Deuxième colonne :", X_example[:, 1])

In [ ]:
# liste les points dans les données

for i in range(X_example.shape[0]):
    print("Point numéro " + str(i) + " dans les données :", X_example[i])

De plus, nous allons utiliser matplotlib pour visualiser les résultats.
Pour cela, nous utilisons la fonction `plt.scatter` qui permet d'afficher une liste de points.
Cette fonction a deux arguments obligatoires :

1. la liste des coordonnées horizontales de tous les points
2. la liste des coordonnées verticales de tous les points

In [ ]:
plt.scatter(X_example[:, 0], X_example[:, 1])

Regardez bien le graphe créé ci-dessus : l'échelle peut parfois être trompeuse !
Pour cela, on peut la fixer grâce aux fonction `plt.xlim` et `plt.ylim`.

In [ ]:
plt.xlim(0, 3)  # valeurs max et min sur l'axe horizontal
plt.ylim(0, 3)  # valeurs max et min sur l'axe vertical
plt.scatter(X_example[:, 0], X_example[:, 1])

Nous pouvons également donner une couleur aux points.
Pour cela, il faut renseigner un 3ème paramêtre `c` contenant la classe à laquelle chaque point est associé.
La classe de chaque point doit être un entier, 0 étant la première classe, 1 la seconde, etc etc.

In [ ]:
# On a 3 points de données,
# donc on créé un vecteur d'entiers avec 3 valeurs
# qui associe chaque point à une classe
y_example = np.array(
    [0, 1, 1],  # le premier point est dans la classe 0, les deux suivants dans la classe 1
    dtype=np.int_
)

# et maintenant l'affichage avec la couleur
plt.scatter(
    X_example[:, 0],
    X_example[:, 1],
    c=y_example,  # la classe de chaque point
    # Et en dernier le jeu de couleurs à utiliser, c'est important de la spécifier.
    # D'autres couleurs sont possibles, voir ici : https://matplotlib.org/stable/users/explain/colors/colormaps.html#qualitative
    # (attention à bien spécifier un jeu de couleurs de la section "qualitative")
    cmap=matplotlib.cm.Set1
)

In [ ]:
# un autre exemple
y_example = np.array(
    [0, 1, 2],  # chaque point est dans sa propre classe
    dtype=np.int_
)

# et maintenant l'affichage avec la couleur
plt.scatter(
    X_example[:, 0],
    X_example[:, 1],
    c=y_example,  # la classe de chaque point
    cmap=matplotlib.cm.Set1  # le jeu de couleurs à utiliser
)

Si votre vision  ne vous permet pas de distinguer les couleurs,
il est toujours possible d'utiliser des marqueurs de point différents,
cela nécessite cependant un peu plus de travail.

In [ ]:
y_example = np.array(
    [0, 1, 1],
    dtype=np.int_
)

# et maintenant l'affichage avec des marqueurs différents

# classe 0 avec une étoile
plt.scatter(
    X_example[y_example == 0, 0],
    X_example[y_example == 0, 1],
    marker="*"
)

# classe 1 avec un point
plt.scatter(
    X_example[y_example == 1, 0],
    X_example[y_example == 1, 1],
    marker="o"
)

In [ ]:
# autre exemple avec 3 classes
# il est plus simple de faire une boucle for
# que de lister explicitement toutes les classes

y_example = np.array(
    [0, 1, 2],
    dtype=np.int_
)

# si vous avez plus de classes,
# vous pouvez ajouter d'autres marqueurs,
# voir ici : https://matplotlib.org/stable/api/markers_api.html

markers = ["*", "o", "+", "x"]
for i in range(0, np.max(y_example) + 1):
    plt.scatter(
        X_example[y_example == i, 0],
        X_example[y_example == i, 1],
        marker=markers[i]
    )

## 2. Clustering hierarchique dans scikit-learn

Nous allons nous intéresser ici uniquement au clustering ascendant (ou agglomératif).
La libraire scikit-learn implémente cette méthode dans la classe `AgglomerativeClustering`.

L'objectif de ce TP est de comparer comment la méthode se comporte en fonction des différents hyperparamètres.
Nous allons en particuliers nous focaliser sur les hyperparamètres suivants :

- n_clusters : nombre de clusters à trouver dans les données
- metric : la métrique (distance) à utiliser. On se limitera à la distance euclidienne/l2 dans le cadre de ce TP, mais par prudence il faudra toujours la renseigner
- linkage : le critère de distance entre clusters à utiliser, les quatres valeurs possibles sont "ward", "complete", "average", "single"

La documentation de cette classe est disponible ici : https://scikit-learn.org/stable/modules/generated/sklearn.cluster.AgglomerativeClustering.html#sklearn.cluster.AgglomerativeClustering

Pour clusteriser les données, nous avons besoin de 3 étapes :

1. créer une instance de la classe `AgglomerativeClustering` en lui indiquant les hypeparamètres qui nous intéressent
2. lancer la procédure de clustering sur les données
3. récupérer la partition des données (où il y aura un nombre de classes égal à l'hyperparamètre `n_clusters`)

In [ ]:
# Petit jeu de données de test
X_example = np.array([
    [1., 1.],  # premier point des données
    [2., 1.],  # deuxième point des données
    [2., 1.2]  # troisième point des données
])

# 1. création de l'instance de AgglomerativeClustering avec les bon hyperparamètres

# notre instance s'appelle model_example,
# on devra donc faire explicitement référence à celle-ci
# pour la manipuler (voir les 2 autres étapes ci-dessous)
model_example = sklearn.cluster.AgglomerativeClustering(
    n_clusters=2,  # nombre de clusters à trouver
    metric="l2",  # distance à utiliser entre les points
    linkage="single"  # critère à utiliser pour la distance entre les clusters
)

# 2. on lance le clustering des données
#   (on le lance spécifiquement pour l'instance model_example qu'on a créé ci-dessus)
model_example.fit(X_example)

# 3. on récupère la partionnement des données.
#    Celui-ci est enregistré dans l'attribut labels_
#    Attention, il faut bien récupérer l'attribut pour l'instance
#    sur laquelle on travaille, ici model_example
y_predicted = model_example.labels_



# on peut maintenant visualiser le partionnement des données,
# par exemple en affichant directement y_predicted
# (vecteurs de 0 et de 1 vu qu'on a que 2 classes)
print("Partitionnement des données :", y_predicted)

# ou sous forme d'un graphe !
plt.xlim(0, 3)  # on fait bien attention à l'échelle
plt.ylim(0, 3)
plt.scatter(
    X_example[:, 0],
    X_example[:, 1],
    c=y_predicted,  # Le partitionnement des données que l'on a récupéré à l'étape 3 ci-dessus
    cmap=matplotlib.cm.Set1
)

## 3. Comparaison entre les différents critères de distance

Nous allons maintenant visualiser le partionnement obtenu à partir de différents critères de distance entre les clusters.
L'objectif est de développer une intuition sur quel est le meilleur critère à utiliser en fonction des connaissances que nous avons sur les données et ce que nous cherchons.

Pour tous les exemples ci-dessous, vous devez :
1. créez les données (i.e. la matrice X)
2. affichez les résultats obtenus avec les 4 critères possibles : "ward", "complete", "average", "single"
3. affichez aussi les résultats avec différents nombres de groupes : 2 groupes et 10 groupes
4. analysez les résultats : que pouvez-vous dire sur les partitions obtenues ?

### Exemple du TD

Nous allons commencer simplement recréer les données de l'exemple du TD et afficher les résultats obtenu avec les différents critères.
Vous trouverez une illustration des données ici : http://caio-corro.fr/sd/exemple_clustering_hierarchique.png

**Commentaire :** pas besoin de faire varier le nombres de groupes pour cette exemple, utilisez seulement 2 groupes.

In [ ]:
# créer les données similaires à celles sur l'image pointé par le lien ci-dessus

# TODO TODO TODO

### Demi-lunes

À partir d'ici, vous devez aussi faire varier le nombre de groupes !

Générez des demi-lunes en utilisans la fonction dédiée dans scikit-learn : https://scikit-learn.org/stable/modules/generated/sklearn.datasets.make_moons.html

Vous pouvez regarder deux cas différents :

1. échantillons de 100 points avec noise à 0
2. échantillons de 500 points avec noise à 0.1

**Remarque :** la fonction retourne deux arrays numpy, (1) la matrice avec les données et (2) un partitionnement de référence. L'exemple ci-dessous explique comment cela fonctionne en Python.

In [ ]:
def fonction_blabla():
    # la fonction retourne deux valeurs
    return "maison", 10

# on peut récupérer chaque valeur de retour
# dans une variable spécifique de la façon suivante
mot, nombre = fonction_blabla()

print(mot)
print(nombre)

In [ ]:
# TODO TODO TODO

### Cercles imbriquées

Nous allons maintenant créer des cercles imbriqués avec la fonction suivante : https://scikit-learn.org/stable/modules/generated/sklearn.datasets.make_circles.html

Vous devez tester les méthodes de clustering sur deux jeux de données différent :
1. Générez 200 points avec un bruit égal à 0.02 et factor égal à 0.7
2. Générez 200 points avec un bruit égal à 0.03 et factor égal à 0.1

In [ ]:
# TODO TODO TODO

### Données non structurées

Vous allez maintenant observer le comportement sur des données non structurées, générées par le bout de code ci-dessous.

In [ ]:
rng = np.random.RandomState(243564)
X_noise = rng.rand(2000, 2)

plt.scatter(X_noise[:, 0], X_noise[:, 1])

In [ ]:
# TODO TODO TODO

## 5. Dendrogramme

Nous allons maintenant visualiser le clustering hierarchique en utilisant un dendrogramme.
Vous pouvez commencer par :

1. Lire la page qui explique comment faire cela dans la documentation de scikit-learn : https://scikit-learn.org/stable/auto_examples/cluster/plot_agglomerative_dendrogram.html
2. Regarder rapidement la documentation de la fonction `dendrogram` : https://docs.scipy.org/doc/scipy/reference/generated/scipy.cluster.hierarchy.dendrogram.html#scipy.cluster.hierarchy.dendrogram

En particulier, dans notre cas :

- vous pouvez copier/coller la fonction `plot_dendrogram` pour la réutiliser telle quelle
- par contre, on n'utilisera pas les arguments `truncate_mode` et `p`, vous pouvez juste les enlever dans l'appel de la fonction
- vous pouvez utiliser l'argument `orientation` pour rendre la figure plus lisible
- ajouter l'argument `labels=word_labels` pour afficher les mots dans la légende, sinon il est impossible d'interpréter le dendrogramme !
- lors de l'instance de `AgglomerativeClustering`, il faut ne pas oublier de donner les argumets `n_clusters=None` et `distance_threshold=0`, sinon la fonction `fit` ne créera pas toutes les informations nécessaires à l'affichage du dendrogramme


Pour cet exercice, nous allons visualiser le clustering de plongements de mots, que vous pouvez télécharger sur la page du cours.
Ces plongements proviennent d'ici : https://marcobaroni.org/composes/semantic-vectors.html
On va utiliser les "best reduced count vectors", qui sont des vecteurs créés par construction d'une table de co-occurence puis réduction de dimension (comme vous avez vu dans le chapitre précédent !).
Vu que ces fichiers contiennent un très grand nombre de mots, j'ai filtré et gardé seulement les plongements de 27 mots.

**Todo :** comparez les dendrogrammes obtenus avec différents critères de distance entre clusters.

In [ ]:
# lecture des plongements de mots
# X_words contient dans chaque ligne un plongement
# et word_labels la liste des mots dont les plongements sont dans X_words

word_labels = list()
X_words = np.zeros((27, 500))
with open("./word_embeddings.txt") as instream:
    for idx, line in enumerate(instream):
        vec = line.strip().split()
        word_labels.append(vec[0])
        X_words[idx] = vec[1:]
        
print(word_labels)

In [ ]:
# TODO TODO TODO